In [1]:
import os
import sys
import argparse

import numpy as np
import pandas as pd
import torch
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns

import scanpy as sc
import scvi
import anndata

import scanpy.external as sce
from scvi.model.utils import mde

from sklearn.metrics import classification_report
from sklearn.metrics.pairwise import cosine_similarity

import scarches
from scarches.dataset.trvae.data_handling import remove_sparsity
from scarches.models.scpoli import scPoli

Global seed set to 0
/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/pytorch_lightning/utilities/warnings.py:53: LightningDeprecationWarning: pytorch_lightning.utilities.warnings.rank_zero_deprecation has been deprecated in v1.6 and will be removed in v1.8. Use the equivalent function from the pytorch_lightning.utilities.rank_zero module instead.
  new_rank_zero_deprecation(
/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/pytorch_lightning/utilities/warnings.py:58: LightningDeprecationWarning: The `pytorch_lightning.loggers.base.rank_zero_experiment` is deprecated in v1.7 and will be removed in v1.9. Please use `pytorch_lightning.loggers.logger.rank_zero_experiment` instead.
  return new_rank_zero_deprecation(*args, **kwargs)
 captum (see https://github.com/pytorch/captum).


## Specify working directory

In [2]:
WD = "/dss/dssfs02/lwp-dss-0001/pn36po/pn36po-dss-0001/di93vel/atlas_building"

## Specify parameters´

In [3]:
o = dict({
    "inti_method": "scpoli",
    "project_name": "lung",
    "annotation": "sample_annot6",
    "out_dir": "new_20230627",
    "project_dir": WD,
})

## Functions

In [4]:
def read_samples(project_dir, sample_sheet, annot_dir):
    adata_list=[]
    print("Loading...")
    for sample in sample_sheet.sample_id:
        sample_file=f"{project_dir}/data/h5ad_pyraw/cp_h5ad/{sample}_pyraw.h5ad"
        adata0 = sc.read_h5ad(sample_file)
        
        adata0.X = adata0.X.astype(np.float32)
        adata0.obs['sample_id'] = sample
        adata0.var = adata0.var.drop(adata0.var.columns, axis=1)
        
        meta_file = f"{annot_dir}/{sample}_annotation.txt"
        if os.path.exists(meta_file) and os.path.getsize(meta_file)>1:
            meta_data = pd.read_csv(meta_file, sep="\t", index_col=0)
            adata0.obs = pd.merge(adata0.obs, meta_data, left_index=True, right_index=True)
        else:
            adata0.obs['level_1'] = 'epithelial'
            adata0.obs['level_2'] = 'na'

        adata_list.append(adata0)
        pub = sample_sheet[sample_sheet['sample_id'] == sample]['publication'].values[0]
        print(pub)
    adata = anndata.AnnData.concatenate(*adata_list, join='outer', fill_value=0)
    del adata_list
    adata.obs['publication'] = ['_'.join(i.split('_')[:3]) for i in adata.obs.sample_id.tolist()]

    adata.obs.index.name = "cells"
    
    # adata.obs['publication'] = ["_".join(i.split('_')[:3]) for i in adata.obs.sample_id.tolist()]
    # adata = qsc.add_yu_meta_data(adata)
    # adata.obs = adata.obs.drop(columns=['Selected_for_epi_comparison_with_tHIO_and_vivo'])
    # adata.obs.Cell_type.fillna('na', inplace=True)

    return adata

In [5]:
def clear_genes(adata):
    clear_genes = pd.read_csv(os.path.join(WD, "data/hg_genes_clear.txt"), header=None)[0].tolist()
    sub_clear_genes = [i for i in clear_genes if i in adata.var.index.tolist()]
    adata = adata[:, sub_clear_genes]
    
    return adata

In [6]:
def pre_inti(adata, project_name):
    adata.layers['counts'] = adata.X
    sc.pp.normalize_total(adata, target_sum=1e4)
    sc.pp.log1p(adata)
    adata.raw = adata
    sc.pp.highly_variable_genes(adata, n_top_genes=3000, batch_key='sample_id')
    adata = adata[:,adata.var.highly_variable]
    # sc.pp.scale(adata)
    # sc.tl.pca(adata, svd_solver='arpack')
    return adata

In [7]:
early_stopping_kwargs = {
    "early_stopping_metric": "val_prototype_loss",
    "mode": "min",
    "threshold": 0,
    "patience": 20,
    "reduce_lr": True,
    "lr_patience": 13,
    "lr_factor": 0.1,
}

def run_scpoli(adata):
    scpoli_model = scPoli(
        adata=adata,
        unknown_ct_names=['na'],
        condition_keys=['sample_id','publication'],
        cell_type_keys=['level_2'],
        embedding_dims=10,
        hidden_layer_sizes=[512, 512]
    )

    scpoli_model.train(
        n_epochs=50,
        pretraining_epochs=4,
        early_stopping_kwargs=early_stopping_kwargs,
        eta=10,
        alpha_epoch_anneal=100
    )

    adata.obsm["X_scPoli"] = scpoli_model.get_latent(
        adata,
        mean=True
    )
    sc.pp.neighbors(adata, use_rep="X_scPoli")
    sc.tl.leiden(adata)
    sc.tl.umap(adata, min_dist=0.1)
    adata.obsm['X_umap_min'] = adata.obsm['X_umap'].copy()
    sc.tl.umap(adata)

    return adata, scpoli_model

In [8]:
def plot_results(adata, out_folder, project_name, method='scvi', mdist=False):
    if mdist:
        if "level_3" in adata.obs:
            with plt.rc_context():  # Use this to set figure params like size and dpi
                sc.pl.umap(adata, color=["publication", "level_1", "level_2", "level_3"], 
                            ncols=1, frameon=False, show=True)
                plt.savefig(f"{out_folder}/figures/{project_name}_{method}_integration2.png", dpi=300, bbox_inches='tight')
        else:
            with plt.rc_context():  # Use this to set figure params like size and dpi
                sc.pl.umap(adata, color=["publication", "level_1", "level_2"], 
                            ncols=1, frameon=False, show=True)
                plt.savefig(f"{out_folder}/figures/{project_name}_{method}_integration2.png", dpi=300, bbox_inches='tight')
    else:
        if "level_3" in adata.obs:
            with plt.rc_context():  # Use this to set figure params like size and dpi
                sc.pl.umap(adata, color=["publication", "level_1", "level_2", "level_3"], 
                            ncols=1, frameon=False, show=True)
                plt.savefig(f"{out_folder}/figures/{project_name}_{method}_integration.png", dpi=300, bbox_inches='tight')
        else:
            with plt.rc_context():  # Use this to set figure params like size and dpi
                sc.pl.umap(adata, color=["publication", "level_1", "level_2"], 
                            ncols=1, frameon=False, show=True)
                plt.savefig(f"{out_folder}/figures/{project_name}_{method}_integration.png", dpi=300, bbox_inches='tight')

## Create output directory

In [9]:
out_folder = f"{o['project_dir']}/results/{o['out_dir']}"
os.system(f"mkdir -pv {out_folder}/figures")

mkdir: created directory '/dss/dssfs02/lwp-dss-0001/pn36po/pn36po-dss-0001/di93vel/atlas_building/results/new_20230627'
mkdir: created directory '/dss/dssfs02/lwp-dss-0001/pn36po/pn36po-dss-0001/di93vel/atlas_building/results/new_20230627/figures'


0

## Load samples

In [10]:
sample_sheet = pd.read_csv(f"{o['project_dir']}/data/all_samples_sheets_corrected.txt", sep="\t")
if o['project_name']=='gut':
    sample_sheet = sample_sheet
if o['project_name']=='intestine':
    sample_sheet = sample_sheet[sample_sheet.tissue=='intestine']
if o['project_name']=='lung':
    sample_sheet = sample_sheet[sample_sheet.tissue=='lung']
if o['project_name']=='liver_bileduck':
    sample_sheet = sample_sheet[sample_sheet.tissue.isin(['liver', 'bileduck'])]
if o['project_name']=='pancreas':
    sample_sheet = sample_sheet[sample_sheet.tissue.isin(['pancreas'])]

In [11]:
annot_dir = f"{o['project_dir']}/data/{o['annotation']}/"
adata = read_samples(o['project_dir'], sample_sheet, annot_dir)

Loading...
Chan_NatCommun_2022
Chan_NatCommun_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Hoffmann_CommunBiol_2022
Kadur_Nat_2022
Kadur_Nat_2022
Kadur_Nat_2022
Miller_DevCell_2020
Miller_DevCell_2020
Miller_DevCell_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Salahudeen_Nat_2020
Rosado_BioRxiv_2021
Tran_iScience_2022
Lamers_EMBOJ_2021
Lim_CellStemCell_2023
Lim_CellStemCell_2023
He_Cell_2022
He_Cell_2022
He_Cell_2022
He_Cell_2022
He_Cell_2022
He_Cell_2022
He_Cell_2022
He_Cell_2022
Lee_NatCommun_2021B
Suzuki_STARProt_2021
Suzuki_STARProt_2021
Suzuki_STARProt_2021
Suzuki_STARProt_

/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/anndata/_core/anndata.py:1755: FutureWarning: The AnnData.concatenate method is deprecated in favour of the anndata.concat function. Please use anndata.concat instead.

See the tutorial for concat at: https://anndata.readthedocs.io/en/latest/concatenation.html
  warnings.warn(
/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/anndata/_core/merge.py:1111: UserWarning: Only some AnnData objects have `.raw` attribute, not concatenating `.raw` attributes.
  warn(


## Inspect concatenated data

In [12]:
adata

AnnData object with n_obs × n_vars = 239440 × 65250
    obs: 'initial_size_spliced', 'initial_size_unspliced', 'initial_size', 'n_genes_by_counts', 'total_counts', 'total_counts_mt', 'pct_counts_mt', 'total_counts_ribo', 'pct_counts_ribo', 'total_counts_hb', 'pct_counts_hb', 'n_genes', 'sample_id', 'level_1', 'level_2', 'level_3', 'Cell_type', 'n_counts', 'batch', 'publication'
    layers: 'ambiguous', 'spliced', 'unspliced'

In [13]:
# adata.write_h5ad(f"{out_folder}/{o['project_name']}.h5ad", compression="gzip")

In [14]:
print(np.max(adata.X))

25001.0


In [15]:
print(np.min(adata.X))

0.0


## Preprocess data

In [30]:
adata = clear_genes(adata)

In [31]:
adata = pre_inti(adata, o['project_name'])

## Train integration model

In [32]:
adata, model = run_scpoli(adata)

/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/scarches/models/scpoli/scpoli_model.py:138: ImplicitModificationWarning: Trying to modify attribute `.obs` of view, initializing view as actual.
  self.adata.obs['conditions_combined'] = adata.obs[condition_keys].apply(lambda x: '_'.join(x), axis=1)


Embedding dictionary:
 	Num conditions: [50, 12]
 	Embedding dim: [10, 10]
Encoder Architecture:
	Input Layer in, out and cond: 3000 512 20
	Hidden Layer 1 in/out: 512 512
	Mean/Var Layer in/out: 512 10
Decoder Architecture:
	First Layer in, out and cond:  10 512 20
	Hidden Layer 1 in/out: 512 512
	Output Layer in/out:  512 3000 

Initializing dataloaders
Starting training
 |█-------------------| 8.0%  - val_loss:  870.19 - val_cvae_loss:  870.19
Initializing unlabeled prototypes with Leiden with an unknown number of  clusters.
Clustering succesful. Found 48 clusters.
 |████████████████████| 100.0%  - val_loss:  899.99 - val_cvae_loss:  893.39 - val_prototype_loss:    6.60 - val_unlabeled_loss:    0.67 - val_labeled_loss:    0.66


In [33]:
adata

AnnData object with n_obs × n_vars = 239440 × 3000
    obs: 'initial_size_spliced', 'initial_size_unspliced', 'initial_size', 'n_genes_by_counts', 'total_counts', 'total_counts_mt', 'pct_counts_mt', 'total_counts_ribo', 'pct_counts_ribo', 'total_counts_hb', 'pct_counts_hb', 'n_genes', 'sample_id', 'level_1', 'level_2', 'level_3', 'Cell_type', 'n_counts', 'batch', 'publication', 'conditions_combined', 'leiden'
    var: 'highly_variable', 'means', 'dispersions', 'dispersions_norm', 'highly_variable_nbatches', 'highly_variable_intersection'
    uns: 'log1p', 'hvg', 'neighbors', 'leiden', 'umap'
    obsm: 'X_scPoli', 'X_umap', 'X_umap_min'
    layers: 'ambiguous', 'spliced', 'unspliced', 'counts'
    obsp: 'distances', 'connectivities'

In [34]:
model.save(f"{out_folder}/model")

In [35]:
plot_results(adata, out_folder, o['project_name'], method='scpoli', mdist=False)

/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/scanpy/plotting/_tools/scatterplots.py:392: UserWarning: No data for colormapping provided via 'c'. Parameters 'cmap' will be ignored
  cax = scatter(
/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/scanpy/plotting/_tools/scatterplots.py:392: UserWarning: No data for colormapping provided via 'c'. Parameters 'cmap' will be ignored
  cax = scatter(
/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/scanpy/plotting/_tools/scatterplots.py:392: UserWarning: No data for colormapping provided via 'c'. Parameters 'cmap' will be ignored
  cax = scatter(
/dss/dsshome1/06/di93vel/.conda/envs/heoa_venv/lib/python3.9/site-packages/scanpy/plotting/_tools/scatterplots.py:392: UserWarning: No data for colormapping provided via 'c'. Parameters 'cmap' will be ignored
  cax = scatter(


<Figure size 800x800 with 0 Axes>

In [20]:
# adata.write_h5ad(f"{out_folder}/{o['project_name']}_scpoli_integration.h5ad", compression="gzip")

## Save scPoli embeddings

In [19]:
embed = adata.obsm["X_scPoli"]

In [20]:
embed_adata = anndata.AnnData(embed)

In [21]:
embed_adata.obs = adata.obs.copy()

In [22]:
embed_adata

AnnData object with n_obs × n_vars = 239440 × 10
    obs: 'initial_size_spliced', 'initial_size_unspliced', 'initial_size', 'n_genes_by_counts', 'total_counts', 'total_counts_mt', 'pct_counts_mt', 'total_counts_ribo', 'pct_counts_ribo', 'total_counts_hb', 'pct_counts_hb', 'n_genes', 'sample_id', 'level_1', 'level_2', 'level_3', 'Cell_type', 'n_counts', 'batch', 'publication', 'conditions_combined', 'leiden'

In [23]:
embed_adata.write_h5ad(f"{out_folder}/{o['project_name']}_scpoli_latent.h5ad", compression="gzip")

## Load trained model

In [25]:
my_obs = sc.read_h5ad(f"{out_folder}/{o['project_name']}_scpoli_latent.h5ad")
adata.obs = my_obs.obs.copy()

In [30]:
model_path = f"{out_folder}/model"
saved_model = scarches.models.scpoli.scPoli.load(model_path, adata)

AnnData object with n_obs × n_vars = 239440 × 3000
    obs: 'initial_size_spliced', 'initial_size_unspliced', 'initial_size', 'n_genes_by_counts', 'total_counts', 'total_counts_mt', 'pct_counts_mt', 'total_counts_ribo', 'pct_counts_ribo', 'total_counts_hb', 'pct_counts_hb', 'n_genes', 'sample_id', 'level_1', 'level_2', 'level_3', 'Cell_type', 'n_counts', 'batch', 'publication', 'conditions_combined', 'leiden'
    var: 'highly_variable', 'means', 'dispersions', 'dispersions_norm', 'highly_variable_nbatches', 'highly_variable_intersection'
    uns: 'log1p', 'hvg'
    layers: 'ambiguous', 'spliced', 'unspliced', 'counts'
Embedding dictionary:
 	Num conditions: [50]
 	Embedding dim: [3]
Encoder Architecture:
	Input Layer in, out and cond: 3000 489 3
	Mean/Var Layer in/out: 489 10
Decoder Architecture:
	First Layer in, out and cond:  10 489 3
	Output Layer in/out:  489 3000 



In [40]:
dir(saved_model.model)

['T_destination',
 '__annotations__',
 '__call__',
 '__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattr__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__setstate__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_apply',
 '_backward_hooks',
 '_backward_pre_hooks',
 '_buffers',
 '_call_impl',
 '_forward_hooks',
 '_forward_hooks_with_kwargs',
 '_forward_pre_hooks',
 '_forward_pre_hooks_with_kwargs',
 '_get_backward_hooks',
 '_get_backward_pre_hooks',
 '_get_name',
 '_is_full_backward_hook',
 '_load_from_state_dict',
 '_load_state_dict_post_hooks',
 '_load_state_dict_pre_hooks',
 '_maybe_warn_non_full_backward_hook',
 '_modules',
 '_named_members',
 '_non_persistent_buffers_set',
 '_parameters',
 '_register_load_state_dict_pre_hook',
 '_register_sta

In [41]:
dir(saved_model.model.embeddings)

['T_destination',
 '__add__',
 '__annotations__',
 '__call__',
 '__class__',
 '__delattr__',
 '__delitem__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattr__',
 '__getattribute__',
 '__getitem__',
 '__gt__',
 '__hash__',
 '__iadd__',
 '__init__',
 '__init_subclass__',
 '__iter__',
 '__le__',
 '__len__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__setitem__',
 '__setstate__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_apply',
 '_backward_hooks',
 '_backward_pre_hooks',
 '_buffers',
 '_call_impl',
 '_forward_hooks',
 '_forward_hooks_with_kwargs',
 '_forward_pre_hooks',
 '_forward_pre_hooks_with_kwargs',
 '_get_abs_string_index',
 '_get_backward_hooks',
 '_get_backward_pre_hooks',
 '_get_name',
 '_is_full_backward_hook',
 '_load_from_state_dict',
 '_load_state_dict_post_hooks',
 '_load_state_dict_pre_hooks',
 '_maybe_warn_non_full_backward_hook',
 '_modules

In [43]:
conditional_embeddings = saved_model.get_conditional_embeddings()
conditional_embeddings

AnnData object with n_obs × n_vars = 50 × 3

In [44]:
conditional_embeddings.write_h5ad(f"{out_folder}/{o['project_name']}_conditional_embeddings.h5ad")